In [1]:
%load_ext rpy2.ipython

In [2]:
%%R
set.seed(88888888) # maximum luck

library(DESeq2)
library(plotly)
library(ggplot2)
library(viridis)
library(magrittr)
library(pheatmap)
library(DescTools)
library(pdfCluster)
library(RColorBrewer)
library(SummarizedExperiment)
library(caret)
library(class)
library(htmlwidgets)

Loading required package: S4Vectors
Loading required package: stats4
Loading required package: BiocGenerics

Attaching package: ‘BiocGenerics’

The following objects are masked from ‘package:stats’:

    IQR, mad, sd, var, xtabs

The following objects are masked from ‘package:base’:

    anyDuplicated, aperm, append, as.data.frame, basename, cbind,
    colnames, dirname, do.call, duplicated, eval, evalq, Filter, Find,
    get, grep, grepl, intersect, is.unsorted, lapply, Map, mapply,
    match, mget, order, paste, pmax, pmax.int, pmin, pmin.int,
    Position, rank, rbind, Reduce, rownames, sapply, setdiff, sort,
    table, tapply, union, unique, unsplit, which.max, which.min


Attaching package: ‘S4Vectors’

The following object is masked from ‘package:utils’:

    findMatches

The following objects are masked from ‘package:base’:

    expand.grid, I, unname

Loading required package: IRanges
Loading required package: GenomicRanges
Loading required package: GenomeInfoDb
Loading require

In [3]:
%%R
OUT_DIR <- "/mnt/home/yuankeji/RanceLab/reticula_new/reticula/data/tcdd/output/"
N_FOLDS <- 10

In [4]:
%%R
vst.counts <- readRDS(paste(OUT_DIR, "vst_counts0.3vs0_time_course.Rds", sep = ""))
print(vst.counts)

class: DESeqTransform 
dim: 9297 91 
metadata(1): version
assays(1): ''
rownames(9297): ENSMUSG00000000001 ENSMUSG00000000028 ...
  ENSMUSG00000118462 ENSMUSG00000118541
rowData names(4): baseMean baseVar allZero dispFit
colnames(91): SRR7817611 SRR7817612 ... SRR4317611 SRR4317612
colData names(3): Sample Dose sizeFactor


In [5]:
%%R
sample <- colData(vst.counts)
# print(sample)

In [6]:
%%R
vst.count.mtx <-
   vst.counts %>% SummarizedExperiment::assay() %>% as.data.frame()
print(length(vst.count.mtx))
 head(vst.count.mtx)

[1] 91
                   SRR7817611 SRR7817612 SRR7817614 SRR7817615 SRR7817616
ENSMUSG00000000001   15.60498   15.61890   15.56213   15.63875   15.61549
ENSMUSG00000000028   10.08665    9.94813   10.18500   10.03871   10.10636
ENSMUSG00000000049   19.68607   19.66149   19.91928   19.89180   19.89678
ENSMUSG00000000058   10.66183   10.79316   10.82456   10.55333   11.06405
ENSMUSG00000000085   12.32036   12.08760   12.22955   12.23284   11.90094
ENSMUSG00000000088   16.54977   16.55070   16.52094   16.25248   16.21137
                   SRR7817623 SRR7817624 SRR7817625 SRR7817626 SRR7817627
ENSMUSG00000000001   15.54497   15.57088  15.712787   15.68877   15.52643
ENSMUSG00000000028   10.25885   10.07846   9.978545   10.13579   10.64073
ENSMUSG00000000049   19.91051   19.88307  19.823470   19.83112   19.84957
ENSMUSG00000000058   10.81314   11.16113  10.595601   10.75627   10.71488
ENSMUSG00000000085   12.05451   12.30390  12.398376   12.25024   11.95668
ENSMUSG00000000088   16.16684  

ENSMUSG00000000085  11.938407   12.07291   12.08404   11.80493   12.28004
ENSMUSG00000000088  15.860309   15.84776   16.02172   16.04734   15.09810
                   SRR4317631 SRR4317632 SRR4317633 SRR4317634 SRR4317635
ENSMUSG00000000001   15.18318   15.16169   15.24972   15.30367   15.34929
ENSMUSG00000000028   10.44142   10.30325   10.26954   10.20561   10.47967
ENSMUSG00000000049   20.08275   20.08824   20.08947   20.07329   19.92597
ENSMUSG00000000058   10.90224   10.98733   11.27601   11.23321   11.37214
ENSMUSG00000000085   12.19814   12.08395   11.89067   11.93171   11.70489
ENSMUSG00000000088   15.16928   15.11233   14.94480   15.04655   14.69200
                   SRR4317636 SRR4317607 SRR4317609 SRR4317610 SRR4317611
ENSMUSG00000000001   15.43865   15.01818   15.24940   15.35179   15.18975
ENSMUSG00000000028   10.43926   10.24136   10.50625   10.32778   10.58927
ENSMUSG00000000049   19.93800   20.05085   20.11331   20.12436   20.10453
ENSMUSG00000000058   11.49373   11.232

In [7]:
%%R
tcdd_dose_detail.vec <-
   readRDS(paste(OUT_DIR, "tcdd_dose_detail_vec0.3vs0_time_course.Rds", sep = ""))
print(tcdd_dose_detail.vec)

 [1] 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
[20] 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0
[39] 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.3 0.3 0.3
[58] 0.3 0.3 0.0 0.0 0.0 0.3 0.3 0.3 0.3 0.3 0.0 0.0 0.0 0.0 0.3 0.3 0.0 0.3 0.3
[77] 0.3 0.3 0.3 0.0 0.3 0.3 0.3 0.3 0.3 0.3 0.0 0.0 0.0 0.0 0.0


In [8]:
%%R
rxn2ensembls.nls <-
   readRDS(paste(OUT_DIR, "rxn2ensembls_nls0.3vs0_time_course.Rds", sep = ""))
print(length(rxn2ensembls.nls))
print(rxn2ensembls.nls)

[1] 9825
$`R-MMU-170666`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSMUSG00000057614"

$`R-MMU-170671`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSMUSG00000057614"

$`R-MMU-170674`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSM

 [46] "ENSMUSG00000028777" "ENSMUSG00000028950" "ENSMUSG00000028971"
 [49] "ENSMUSG00000029064" "ENSMUSG00000029072" "ENSMUSG00000029236"
 [52] "ENSMUSG00000029371" "ENSMUSG00000029372" "ENSMUSG00000029373"
 [55] "ENSMUSG00000029379" "ENSMUSG00000029380" "ENSMUSG00000029417"
 [58] "ENSMUSG00000029530" "ENSMUSG00000029663" "ENSMUSG00000029713"
 [61] "ENSMUSG00000029819" "ENSMUSG00000031778" "ENSMUSG00000031861"
 [64] "ENSMUSG00000031980" "ENSMUSG00000032192" "ENSMUSG00000032562"
 [67] "ENSMUSG00000032766" "ENSMUSG00000033717" "ENSMUSG00000034117"
 [70] "ENSMUSG00000034855" "ENSMUSG00000035042" "ENSMUSG00000035383"
 [73] "ENSMUSG00000035431" "ENSMUSG00000035448" "ENSMUSG00000036353"
 [76] "ENSMUSG00000036362" "ENSMUSG00000036381" "ENSMUSG00000036402"
 [79] "ENSMUSG00000036437" "ENSMUSG00000036832" "ENSMUSG00000037010"
 [82] "ENSMUSG00000037014" "ENSMUSG00000037140" "ENSMUSG00000037346"
 [85] "ENSMUSG00000037944" "ENSMUSG00000038607" "ENSMUSG00000038668"
 [88] "ENSMUSG00000038811" "ENSMUS

 [4] "ENSMUSG00000019775" "ENSMUSG00000020599" "ENSMUSG00000021219"
 [7] "ENSMUSG00000024186" "ENSMUSG00000026357" "ENSMUSG00000026358"
[10] "ENSMUSG00000026475" "ENSMUSG00000026527" "ENSMUSG00000026678"
[13] "ENSMUSG00000028777" "ENSMUSG00000029101" "ENSMUSG00000032562"
[16] "ENSMUSG00000038530" "ENSMUSG00000042671" "ENSMUSG00000051079"
[19] "ENSMUSG00000052087" "ENSMUSG00000057614" "ENSMUSG00000059810"

$`R-MMU-8982019`
 [1] "ENSMUSG00000000001" "ENSMUSG00000002458" "ENSMUSG00000002459"
 [4] "ENSMUSG00000019775" "ENSMUSG00000020599" "ENSMUSG00000021219"
 [7] "ENSMUSG00000024186" "ENSMUSG00000026357" "ENSMUSG00000026358"
[10] "ENSMUSG00000026475" "ENSMUSG00000026527" "ENSMUSG00000026678"
[13] "ENSMUSG00000028777" "ENSMUSG00000029101" "ENSMUSG00000032562"
[16] "ENSMUSG00000038530" "ENSMUSG00000042671" "ENSMUSG00000051079"
[19] "ENSMUSG00000052087" "ENSMUSG00000057614" "ENSMUSG00000059810"

$`R-MMU-8982020`
 [1] "ENSMUSG00000000001" "ENSMUSG00000002458" "ENSMUSG00000002459"
 [4] "ENSMUS

 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000024325" "ENSMUSG00000025577" "ENSMUSG00000025578"
 [7] "ENSMUSG00000026021" "ENSMUSG00000026484" "ENSMUSG00000026739"
[10] "ENSMUSG00000028796" "ENSMUSG00000037652" "ENSMUSG00000039989"
[13] "ENSMUSG00000040669"

$`R-MMU-4570463`
 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000020265" "ENSMUSG00000020738" "ENSMUSG00000024325"
 [7] "ENSMUSG00000025577" "ENSMUSG00000025578" "ENSMUSG00000026484"
[10] "ENSMUSG00000026739" "ENSMUSG00000028796" "ENSMUSG00000031347"
[13] "ENSMUSG00000037652" "ENSMUSG00000039989" "ENSMUSG00000040669"

$`R-MMU-4570499`
 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000020738" "ENSMUSG00000021546" "ENSMUSG00000024325"
 [7] "ENSMUSG00000025577" "ENSMUSG00000025578" "ENSMUSG00000026484"
[10] "ENSMUSG00000026739" "ENSMUSG00000028796" "ENSMUSG00000037652"
[13] "ENSMUSG00000039989" "ENSMUSG00000040669"

$`R-MM

 [1] "ENSMUSG00000000126" "ENSMUSG00000009900" "ENSMUSG00000010797"
 [4] "ENSMUSG00000012282" "ENSMUSG00000015957" "ENSMUSG00000018486"
 [7] "ENSMUSG00000021994" "ENSMUSG00000022382" "ENSMUSG00000022996"
[10] "ENSMUSG00000022997" "ENSMUSG00000026167" "ENSMUSG00000027840"
[13] "ENSMUSG00000028173" "ENSMUSG00000029671" "ENSMUSG00000030093"
[16] "ENSMUSG00000030170" "ENSMUSG00000033227" "ENSMUSG00000036856"
[19] "ENSMUSG00000036961"

$`R-MMU-3781943`
 [1] "ENSMUSG00000000126" "ENSMUSG00000009900" "ENSMUSG00000010797"
 [4] "ENSMUSG00000012282" "ENSMUSG00000015957" "ENSMUSG00000018486"
 [7] "ENSMUSG00000021994" "ENSMUSG00000022382" "ENSMUSG00000022996"
[10] "ENSMUSG00000022997" "ENSMUSG00000026167" "ENSMUSG00000027840"
[13] "ENSMUSG00000028173" "ENSMUSG00000029671" "ENSMUSG00000030093"
[16] "ENSMUSG00000030170" "ENSMUSG00000033227" "ENSMUSG00000036856"
[19] "ENSMUSG00000036961"

$`R-MMU-205328`
[1] "ENSMUSG00000000127" "ENSMUSG00000005672" "ENSMUSG00000019966"
[4] "ENSMUSG00000032113" "ENSM

...

[1] "ENSMUSG00000029238" "ENSMUSG00000037727" "ENSMUSG00000055116"

$`R-MMU-5663185`
[1] "ENSMUSG00000029238" "ENSMUSG00000030256" "ENSMUSG00000055116"

$`R-MMU-5663189`
[1] "ENSMUSG00000029238" "ENSMUSG00000031443" "ENSMUSG00000055116"

$`R-MMU-5669295`
[1] "ENSMUSG00000029238" "ENSMUSG00000032238" "ENSMUSG00000055116"

$`R-MMU-5669318`
[1] "ENSMUSG00000029238" "ENSMUSG00000032238" "ENSMUSG00000055116"

$`R-MMU-879716`
[1] "ENSMUSG00000029238" "ENSMUSG00000030256" "ENSMUSG00000055116"

$`R-MMU-879748`
[1] "ENSMUSG00000029238" "ENSMUSG00000055116" "ENSMUSG00000059824"

$`R-MMU-879779`
[1] "ENSMUSG00000029238" "ENSMUSG00000037727" "ENSMUSG00000055116"

$`R-MMU-879795`
[1] "ENSMUSG00000029238" "ENSMUSG00000030103" "ENSMUSG00000055116"

$`R-MMU-8878686`
[1] "ENSMUSG00000029238" "ENSMUSG00000030087" "ENSMUSG00000055116"

$`R-NUL-4568946`
[1] "ENSMUSG00000029238"

$`R-MMU-111285`
[1] "ENSMUSG00000029246"

$`R-MMU-111289`
[1] "ENSMUSG00000029246"

$`R-MMU-73815`
[1] "ENSMUSG00000029246"

$`R

[4] "ENSMUSG00000054417" "ENSMUSG00000056035" "ENSMUSG00000061292"
[7] "ENSMUSG00000070419" "ENSMUSG00000075551" "ENSMUSG00000075552"

$`R-MMU-211959`
[1] "ENSMUSG00000029630" "ENSMUSG00000029727" "ENSMUSG00000038656"
[4] "ENSMUSG00000054417" "ENSMUSG00000056035" "ENSMUSG00000061292"
[7] "ENSMUSG00000070419" "ENSMUSG00000075551" "ENSMUSG00000075552"

$`R-MMU-213175`
[1] "ENSMUSG00000029630" "ENSMUSG00000029727" "ENSMUSG00000038656"
[4] "ENSMUSG00000054417" "ENSMUSG00000056035" "ENSMUSG00000061292"
[7] "ENSMUSG00000070419" "ENSMUSG00000075551" "ENSMUSG00000075552"

$`R-MMU-5423664`
[1] "ENSMUSG00000029630" "ENSMUSG00000029727" "ENSMUSG00000038656"
[4] "ENSMUSG00000054417" "ENSMUSG00000056035" "ENSMUSG00000061292"
[7] "ENSMUSG00000070419" "ENSMUSG00000075551" "ENSMUSG00000075552"

$`R-MMU-5423672`
 [1] "ENSMUSG00000029630" "ENSMUSG00000029727" "ENSMUSG00000032310"
 [4] "ENSMUSG00000038656" "ENSMUSG00000054417" "ENSMUSG00000056035"
 [7] "ENSMUSG00000061292" "ENSMUSG00000070419" "ENSMUSG00

[1] "ENSMUSG00000030225"

$`R-MMU-1675928`
[1] "ENSMUSG00000030228" "ENSMUSG00000030660"

$`R-MMU-8870489`
[1] "ENSMUSG00000030231" "ENSMUSG00000040428" "ENSMUSG00000041757"

$`R-MMU-879575`
[1] "ENSMUSG00000030235" "ENSMUSG00000030236" "ENSMUSG00000033965"
[4] "ENSMUSG00000038963"

$`R-MMU-194079`
[1] "ENSMUSG00000030236"

$`R-MMU-194083`
[1] "ENSMUSG00000030236"

$`R-MMU-9631987`
[1] "ENSMUSG00000030236"

$`R-MMU-9661397`
[1] "ENSMUSG00000030236"

$`R-MMU-9661799`
[1] "ENSMUSG00000030236"

$`R-MMU-9757010`
[1] "ENSMUSG00000030236" "ENSMUSG00000030737"

$`R-MMU-194130`
[1] "ENSMUSG00000030237"

$`R-MMU-9794270`
[1] "ENSMUSG00000030237"

$`R-MMU-70510`
[1] "ENSMUSG00000030246" "ENSMUSG00000030851" "ENSMUSG00000063229"
[4] "ENSMUSG00000101959"

$`R-MMU-71849`
[1] "ENSMUSG00000030246" "ENSMUSG00000030851" "ENSMUSG00000063229"
[4] "ENSMUSG00000101959"

$`R-MMU-1296024`
[1] "ENSMUSG00000030247" "ENSMUSG00000040136" "ENSMUSG00000096146"

$`R-MMU-1369017`
[1] "ENSMUSG00000030247" "ENSMUSG000

[1] "ENSMUSG00000030826"

$`R-MMU-70724`
[1] "ENSMUSG00000030826"

$`R-MMU-8851711`
[1] "ENSMUSG00000030849"

$`R-MMU-70800`
[1] "ENSMUSG00000030861"

$`R-MMU-156673`
[1] "ENSMUSG00000030867" "ENSMUSG00000032254"

$`R-MMU-156678`
[1] "ENSMUSG00000030867" "ENSMUSG00000044201"

$`R-MMU-156699`
[1] "ENSMUSG00000030867" "ENSMUSG00000031016"

$`R-MMU-2984226`
[1] "ENSMUSG00000030867" "ENSMUSG00000034290"

$`R-MMU-3002798`
[1] "ENSMUSG00000030867"

$`R-MMU-8933547`
[1] "ENSMUSG00000030869" "ENSMUSG00000048755"

$`R-MMU-6814094`
[1] "ENSMUSG00000030881" "ENSMUSG00000060904"

$`R-MMU-2168884`
[1] "ENSMUSG00000030895" "ENSMUSG00000052305" "ENSMUSG00000069919"
[4] "ENSMUSG00000073940"

$`R-MMU-2168886`
[1] "ENSMUSG00000030895"

$`R-MMU-2168897`
[1] "ENSMUSG00000030895" "ENSMUSG00000040249"

$`R-MMU-2230983`
[1] "ENSMUSG00000030895" "ENSMUSG00000040249"

$`R-MMU-5693347`
[1] "ENSMUSG00000030905"

$`R-MMU-70654`
[1] "ENSMUSG00000030934"

$`R-MMU-70666`
[1] "ENSMUSG00000030934"

$`R-MMU-8875039`
[1

[1] "ENSMUSG00000031538" "ENSMUSG00000059481"

$`R-MMU-158781`
[1] "ENSMUSG00000031538"

$`R-MMU-158784`
[1] "ENSMUSG00000031538" "ENSMUSG00000059481"

$`R-MMU-9724745`
[1] "ENSMUSG00000031538" "ENSMUSG00000059481"

$`R-MMU-9724753`
[1] "ENSMUSG00000031538" "ENSMUSG00000059481"

$`R-MMU-549112`
[1] "ENSMUSG00000031545"

$`R-MMU-888614`
[1] "ENSMUSG00000031549"

$`R-MMU-198563`
[1] "ENSMUSG00000031551"

$`R-MMU-8870332`
[1] "ENSMUSG00000031557" "ENSMUSG00000034573" "ENSMUSG00000040268"

$`R-MMU-204364`
[1] "ENSMUSG00000031558"

$`R-MMU-428518`
[1] "ENSMUSG00000031558" "ENSMUSG00000034220"

$`R-MMU-8986258`
[1] "ENSMUSG00000031558" "ENSMUSG00000045382" "ENSMUSG00000061353"

$`R-MMU-9010815`
[1] "ENSMUSG00000031558" "ENSMUSG00000056427"

$`R-MMU-9010872`
[1] "ENSMUSG00000031558" "ENSMUSG00000039952"

$`R-MMU-73596`
[1] "ENSMUSG00000031562"

$`R-MMU-437230`
[1] "ENSMUSG00000031565"

$`R-MMU-9756452`
[1] "ENSMUSG00000031565" "ENSMUSG00000032446" "ENSMUSG00000042821"
[4] "ENSMUSG00000062327"

In [9]:
%%R
rxns <- rxn2ensembls.nls %>% names()

In [10]:
%%R
rxn_knn_misclass_rate.nls <- list()
rxn_knn_ari.nls <- list()
rxn_knn_ecount.nls <- list()
rxn_pca.nls <- list()
count <- 0

In [11]:
%%R
toi_indices <- seq(1,length(tcdd_dose_detail.vec))
print(toi_indices)

In [12]:
%%R
tcdd_dose_detail_vec_tis_of_interest <-
   tcdd_dose_detail.vec[toi_indices]
print(tcdd_dose_detail_vec_tis_of_interest)

In [13]:
%%R
vst.count.mtx.tis_of_interest <- vst.count.mtx[, toi_indices]
print(vst.count.mtx.tis_of_interest)

   9.779047   9.215996   9.596669   9.478351
ENSMUSG00000015452   8.916015   9.482138   9.800821   9.603064   9.921760
ENSMUSG00000015461  13.503118  13.416772  13.426424  13.531748  13.715010
ENSMUSG00000015468  11.169112  10.939793  10.694837  11.149152  11.439974
ENSMUSG00000015474  13.599081  13.753520  13.701677  13.626596  13.299477
ENSMUSG00000015478  14.520400  14.631668  14.744571  14.499854  14.515751
ENSMUSG00000015522  14.325798  14.322979  14.530748  14.276611  14.260494
ENSMUSG00000015533   9.576260   8.915276   9.855594   9.617690   9.602834
ENSMUSG00000015568  13.949458  13.580118  14.292981  14.093901  13.927457
ENSMUSG00000015575  13.786976  13.641080  13.708331  13.865671  13.877656
ENSMUSG00000015579   8.916015   8.915276   8.904921   8.915541   8.915513
ENSMUSG00000015605  12.795403  12.574152  12.385409  12.485772  12.580207
ENSMUSG00000015619   9.487315   8.915276   8.904921   9.483996   9.319903
ENSMUSG00000015627   8.916015   9.318635   8.904921   9.461782   9.

ENSMUSG00000017300   8.916015   8.915276   8.904921   8.915541   8.915513
ENSMUSG00000017307  13.175313  13.262998  13.188390  12.997193  12.971961
ENSMUSG00000017309  12.467512  12.478608  12.330603  12.510086  12.347762
ENSMUSG00000017311   8.916015   8.915276   8.904921   8.915541   8.915513
ENSMUSG00000017316   8.916015   8.915276   8.904921   8.915541   8.915513
ENSMUSG00000017344  20.387519  20.372128  20.363906  20.396084  20.388376
ENSMUSG00000017376  12.394598  12.222738  12.276943  12.147167  12.176632
ENSMUSG00000017390  13.183728  13.045453  13.133805  12.866288  12.728654
ENSMUSG00000017404  14.389937  14.448987  14.705483  14.277806  14.294840
ENSMUSG00000017412  10.930648  11.329400  11.189039  11.136287  11.006494
ENSMUSG00000017428  15.251381  15.166107  15.452523  15.559353  15.501218
ENSMUSG00000017453  17.051624  17.061112  17.429371  17.406210  17.372369
ENSMUSG00000017466  12.062035  12.002924  12.125302  11.917261  11.983702
ENSMUSG00000017485  14.338256  14.3420

ENSMUSG00000000374  13.209988  13.422873  13.565152  13.651671  13.674070
ENSMUSG00000000394   8.914831   8.914527   8.920083   8.919472   8.919140
ENSMUSG00000000399  15.710556  15.711085  15.854989  15.948083  15.896001
ENSMUSG00000000409   9.916435  10.225092   9.971767   9.341015   9.732907
ENSMUSG00000000420  14.247266  14.233195  14.270206  14.075567  14.096618
ENSMUSG00000000435   8.914831   8.914527   8.920083   8.919472   8.919140
ENSMUSG00000000440  12.206006  12.247268  12.174313  11.985913  12.204646
ENSMUSG00000000441  15.854013  15.811605  15.865438  15.923523  15.984195
ENSMUSG00000000489   9.966006   9.846349  10.159415  10.302875  10.429777
ENSMUSG00000000530  10.788341  10.559425  10.803749  11.163206  10.849960
ENSMUSG00000000532  12.894870  12.913762  12.756475  12.875633  12.538193
ENSMUSG00000000552  13.294743  13.137690  12.695361  12.644953  12.812593
ENSMUSG00000000555  13.915843  13.880359  13.795589  13.835121  14.048781
ENSMUSG00000000560   8.914831   8.9145

ENSMUSG00000001473  11.836595  12.191167  12.203098  12.162488  11.835782
ENSMUSG00000001494   9.479018   8.914527   9.344260   9.341015   8.919140
ENSMUSG00000001504   8.914831   8.914527   8.920083   8.919472   8.919140
ENSMUSG00000001506  10.468601  10.704363  10.355501  10.710022  10.922701
ENSMUSG00000001507  11.925653  11.962639  11.647759  11.702996  11.994433
ENSMUSG00000001517  10.078340   9.974199   9.741515   9.735941   9.630272
ENSMUSG00000001518  11.940619  11.758620  12.482441  12.753922  12.575205
ENSMUSG00000001521   9.916435  10.178374  10.525883  10.426013   9.819396
ENSMUSG00000001524  12.241506  12.613228  12.512514  12.543172  12.681045
ENSMUSG00000001525  14.735053  14.701569  15.022867  14.986353  15.057648
ENSMUSG00000001542  15.095366  14.921021  14.939111  14.893605  15.118615
ENSMUSG00000001552  14.138119  14.223391  13.894211  13.929510  14.132833
ENSMUSG00000001622   8.914831   8.914527   8.920083   8.919472   8.919140
ENSMUSG00000001632  12.732663  12.6808

ENSMUSG00000002668  11.432026  11.368505  10.619670  11.079328  10.889683
ENSMUSG00000002679  11.789769  12.041006  12.269239  12.341200  11.992709
ENSMUSG00000002699  11.669517  11.361372  10.860263  10.958248  11.244349
ENSMUSG00000002731  13.104661  13.208449  12.858073  12.848984  12.921433
ENSMUSG00000002733  12.865925  12.497298  12.979664  12.907942  12.959777
ENSMUSG00000002741  14.416565  14.532173  14.708465  14.729108  14.620544
ENSMUSG00000002748  14.792683  14.587853  14.786545  14.846785  14.639316
ENSMUSG00000002763  15.394049  15.428456  15.605607  15.531714  15.753722
ENSMUSG00000002767  14.177471  14.352439  14.430911  14.299734  14.576075
ENSMUSG00000002769  20.238146  20.240068  19.738533  19.737740  20.143456
ENSMUSG00000002771   8.914831   9.314626   8.920083   9.488367   9.274160
ENSMUSG00000002778  15.252411  15.423231  15.390522  15.239745  15.064367
ENSMUSG00000002797  11.489057  11.557341  11.845211  11.652524  12.078433
ENSMUSG00000002799   9.693421   9.7730

...

ENSMUSG00000001525  14.772263  14.698985  14.307420  14.163685  14.195841
ENSMUSG00000001542  15.548732  15.247740  15.371444  15.505042  15.276683
ENSMUSG00000001552  13.984777  13.802297  13.779632  13.651041  13.968220
ENSMUSG00000001622   8.901964   8.921000   8.921878   8.922379   8.914554
ENSMUSG00000001632  12.967664  12.707320  12.891713  12.841767  12.971010
ENSMUSG00000001642  10.487024  10.969510  10.427428  10.438022  10.501074
ENSMUSG00000001656   8.901964   8.921000   8.921878   8.922379   8.914554
ENSMUSG00000001657   8.901964   8.921000   8.921878   8.922379   8.914554
ENSMUSG00000001663  16.853182  16.865696  17.001059  17.055803  16.851610
ENSMUSG00000001670  20.162568  20.364592  20.234064  20.258867  20.122638
ENSMUSG00000001729  14.194222  14.203242  13.865484  13.831822  14.045127
ENSMUSG00000001741  11.288758  11.322391  10.967845  11.187876  11.487970
ENSMUSG00000001750  13.885106  14.599637  13.823999  13.964891  14.434479
ENSMUSG00000001751  13.083055  13.3337

ENSMUSG00000002769  19.462760  20.062386  19.826185  19.815265  19.905992
ENSMUSG00000002771   9.645217   9.423547   9.528147   8.922379   9.674765
ENSMUSG00000002778  15.144083  15.398978  15.065976  15.101505  15.236911
ENSMUSG00000002797  11.671239  11.938165  11.811602  11.856289  11.712806
ENSMUSG00000002799   9.385115   8.921000   9.528147   9.531622   9.477069
ENSMUSG00000002803  11.883604  12.531164  12.223131  12.194398  11.975947
ENSMUSG00000002804  11.914956  12.262823  12.043314  11.932450  12.233592
ENSMUSG00000002814  12.013091  12.260774  11.901588  11.845797  11.979821
ENSMUSG00000002820  13.741320  13.931043  13.579425  13.414084  13.545520
ENSMUSG00000002846  13.138689  13.319180  13.016902  13.104627  13.274738
ENSMUSG00000002847  14.334952  14.659893  14.384103  14.642220  14.574928
ENSMUSG00000002870  10.810050  10.798956  11.046141  10.924699  11.337823
ENSMUSG00000002885  13.195624  13.315618  12.636569  12.770983  13.352703
ENSMUSG00000002900  11.964471  12.1615

ENSMUSG00000003865  10.632886  10.716004  10.712278  10.654327  10.872127
ENSMUSG00000003872   8.901964   8.921000   8.921878   8.922379   9.477069
ENSMUSG00000003873  12.811166  13.053832  12.547720  12.650424  12.726998
ENSMUSG00000003882  10.145674   9.838017   9.997890   9.851800   9.787121
ENSMUSG00000003923  14.403338  14.232206  14.353493  14.557789  14.668855
ENSMUSG00000003934   9.324074   8.921000   8.921878   9.452996   8.914554
ENSMUSG00000003970  16.613591  16.729154  16.445150  16.405102  16.742472
ENSMUSG00000003974   8.901964   8.921000   8.921878   8.922379   8.914554
ENSMUSG00000004018  11.938135  11.796155  12.011426  12.111648  11.844423
ENSMUSG00000004032  11.995966  12.141000  12.301841  12.596347  12.116741
ENSMUSG00000004035  14.864460  14.883092  14.986697  15.029933  14.914104
ENSMUSG00000004038  16.210166  15.372189  15.521093  15.622452  15.222785
ENSMUSG00000004040  15.854640  15.934633  15.836989  15.868981  16.051415
ENSMUSG00000004043  12.887374  13.3015

ENSMUSG00000005089  17.504580  16.832052  17.122408  17.134807  17.082278
ENSMUSG00000005102  12.262309  12.503195  12.221256  12.569639  12.298417
ENSMUSG00000005103  14.362975  14.396908  14.245214  14.174702  14.522334
ENSMUSG00000005107  14.906821  14.429390  14.496904  14.507350  14.610348
ENSMUSG00000005142  16.356163  15.999819  15.801057  15.778000  16.237354
ENSMUSG00000005148   9.490163   9.349132   9.654724   9.531622   9.310697
ENSMUSG00000005150  13.302518  13.435097  13.372303  13.137106  13.332018
ENSMUSG00000005161  15.748207  15.762493  15.803790  15.831182  15.664840
ENSMUSG00000005198  14.640741  14.728261  14.622672  14.644766  14.536267
ENSMUSG00000005204  13.828732  13.763306  13.709026  13.551131  14.074578
ENSMUSG00000005220   9.387456   9.647604   8.921878   9.658793   9.314769
ENSMUSG00000005225  13.699150  13.311635  13.713439  13.360583  13.960110
ENSMUSG00000005232   9.060347   9.522065  10.011551   9.909921   8.914554
ENSMUSG00000005233  11.054797  11.2614

ENSMUSG00000006301  15.000826  14.716618  14.631355  14.538435  14.695541
ENSMUSG00000006304  15.074544  15.268579  15.084264  15.196376  15.266255
ENSMUSG00000006307  14.022833  13.782245  13.713219  13.691767  14.042804
ENSMUSG00000006333  17.066157  17.004493  16.826537  16.823340  16.725385
ENSMUSG00000006335  12.023176  12.365381  12.028349  11.930192  12.215083
ENSMUSG00000006344  10.845056  11.006652  10.665865  10.861961  11.001162
ENSMUSG00000006345   9.246777   9.349132   8.921878   9.356443   9.314769
ENSMUSG00000006373  19.558913  19.459348  19.462390  19.462085  19.526280
ENSMUSG00000006386  12.182259  11.922555  12.434926  12.359887  12.670587
ENSMUSG00000006390  13.792412  13.986716  13.563088  13.585713  13.999872
ENSMUSG00000006392  14.296405  14.446542  14.152071

In [14]:
%%R
training_indices <-
   caret::createDataPartition(
      tcdd_dose_detail_vec_tis_of_interest,
      times = 1,
      p = 1.0, # no data will be held out when set to "1.0"
      list = FALSE
   )
print(training_indices)

In [15]:
%%R
vst.count.mtx.train <-
   vst.count.mtx.tis_of_interest[, training_indices] #9/10ths of data
vst.count.mtx.test  <-
   vst.count.mtx.tis_of_interest[, -training_indices] #1/10th of data

print(vst.count.mtx.train)

  14.201581  14.270970  14.074809  13.858120  14.207519
ENSMUSG00000014504  12.996710  12.901716  13.414907  13.444591  12.950354
ENSMUSG00000014550  12.456820  12.757206  12.786682  12.760000  12.627869
ENSMUSG00000014551  13.994700  14.109845  14.103181  14.075234  14.106356
ENSMUSG00000014554  12.379542  12.693767  13.089090  12.922031  12.908957
ENSMUSG00000014599  12.191182  12.497677  12.178530  12.121400  11.780537
ENSMUSG00000014602   9.290992   9.816502   9.344260   9.511447   8.919140
ENSMUSG00000014606  15.127234  15.185429  15.031224  14.911392  15.072528
ENSMUSG00000014609   9.273041   9.341889   9.486486   9.341015   9.442755
ENSMUSG00000014704   9.848259   9.846349   9.515692   8.919472   9.614619
ENSMUSG00000014763  13.545988  13.405273  13.798998  13.925408  13.619955
ENSMUSG00000014767  13.698013  13.733831  13.745861  13.674719  13.596761
ENSMUSG00000014769  15.878191  15.851129  15.837079  15.851638  15.783653
ENSMUSG00000014773  11.348620  11.426614  11.328873  11.

ENSMUSG00000016181  12.023909  11.828700  12.114946  12.153561  12.152944
ENSMUSG00000016194  18.474223  18.468792  18.385009  18.360373  18.304619
ENSMUSG00000016206  11.036360  10.802330  10.669938  11.221064  11.125761
ENSMUSG00000016252  15.437150  15.436892  15.726044  15.798323  15.894838
ENSMUSG00000016253  13.704352  13.599778  13.689980  13.972813  14.035390
ENSMUSG00000016255   9.776133   9.314626   9.344260   9.341015   8.919140
ENSMUSG00000016256  16.771094  16.738800  16.634991  16.686039  16.657715
ENSMUSG00000016283   9.479018   8.914527   8.920083   8.919472   8.919140
ENSMUSG00000016308  13.515917  13.493461  13.240519  13.521095  13.430134
ENSMUSG00000016319  17.497526  17.522549  17.360908  17.424340  17.626742
ENSMUSG00000016327   8.914831   8.914527   8.920083   8.919472   8.919140
ENSMUSG00000016356  10.853489  10.736875  10.932986  11.024261  10.759325
ENSMUSG00000016409  12.154592  12.227589  12.394906  12.333410  12.377359
ENSMUSG00000016427  14.189090  14.0179

ENSMUSG00000018068  11.546511  11.488266  11.982714  12.218375  11.919853
ENSMUSG00000018102  15.920253  15.939389  15.926028  15.857665  16.196571
ENSMUSG00000018126   8.914831   8.914527   8.920083   8.919472   8.919140
ENSMUSG00000018143  13.378924  13.490312  13.005356  13.062506  13.005645
ENSMUSG00000018160  13.807640  13.800537  13.478399  13.496972  13.514144
ENSMUSG00000018166  16.726507  16.745303  16.460222  16.411581  16.877423
ENSMUSG00000018167  12.994576  12.967003  12.704641  12.750413  12.827902
ENSMUSG00000018169   9.889102  10.270565  10.040965   9.817818  10.361446
ENSMUSG00000018189  13.180417  13.018058  13.192988  13.283123  13.254089
ENSMUSG00000018209  13.373253  13.220102  13.099957  12.970438  13.183392
ENSMUSG00000018263   8.914831   8.914527   8.920083   8.919472   8.919140
ENSMUSG00000018286  15.766449  15.663525  15.690866  15.773097  15.633508
ENSMUSG00000018293  16.143704  16.206916  16.124023  16.182783  16.286728
ENSMUSG00000018326  15.550882  15.5871

ENSMUSG00000000958  11.050384  10.434322  10.547849  10.880378  11.054811
ENSMUSG00000000959  14.673856  14.387132  14.527833  14.808703  14.766392
ENSMUSG00000000982   9.335403   8.927484   8.927363   9.304892   9.305656
ENSMUSG00000001014  10.013214   8.927484   9.521701   9.949568   9.305656
ENSMUSG00000001016  13.099834  13.119694  13.097900  13.235372  13.053690
ENSMUSG00000001017  14.618960  14.401895  14.421893  14.638658  14.661651
ENSMUSG00000001018  13.436538  13.612710  13.712451  13.369994  13.493792
ENSMUSG00000001029  10.286159  10.513805  10.581872  10.445273  10.650880
ENSMUSG00000001034  10.859068  11.166204  10.681110  10.890184  10.794013
ENSMUSG00000001036  12.003781  12.101836  12.178943  12.132347  12.178601
ENSMUSG00000001039   9.800782   9.986346   9.382738   9.670422   9.289375
ENSMUSG00000001052  13.613166  13.731173  13.663536  13.752114  13.716362
ENSMUSG00000001056  13.186185  12.769557  12.830620  12.971102  12.680306
ENSMUSG00000001095  12.062215  10.9643

ENSMUSG00000002068   9.812158  10.184640  10.515636  10.109666  10.016091
ENSMUSG00000002100   9.335403   8.927484   8.927363   8.912711   8.912854
ENSMUSG00000002102  15.933281  15.800660  15.747930  16.005851  16.008291
ENSMUSG00000002108  15.712610  15.379099  15.402309  15.710091  15.668034
ENSMUSG00000002109  12.478125  12.949729  12.757789  12.722277  12.693606
ENSMUSG00000002111  11.049877  10.258262  10.365355  11.134356  10.787160
ENSMUSG00000002129  13.606477  12.810953  12.922287  13.472733  13.273057
ENSMUSG00000002147  14.852853  15.157184  15.120178  15.087462  15.078056
ENSMUSG00000002204   9.887107   8.927484   9.807664   8.912711   9.305656
ENSMUSG00000002205  13.487259  13.339452  13.276554  13.438049  13.518099
ENSMUSG00000002210  12.521369  11.991134  11.786535  11.987569  12.096408
ENSMUSG00000002221  13.048531  12.935594  13.152591  13.432561  13.275919
ENSMUSG00000002227  12.970660  13.682302  13.620420  13.587063  13.446046
ENSMUSG00000002233  11.435306  10.9795

...

ENSMUSG00000000149  15.913736
ENSMUSG00000000154  15.858417
ENSMUSG00000000168  14.415193
ENSMUSG00000000171  16.775295
ENSMUSG00000000182   8.914531
ENSMUSG00000000183   8.914531
ENSMUSG00000000184  12.208034
ENSMUSG00000000197   8.914531
ENSMUSG00000000214   8.914531
ENSMUSG00000000215   8.914531
ENSMUSG00000000216   8.914531
ENSMUSG00000000223   8.914531
ENSMUSG00000000247  10.660190
ENSMUSG00000000253  10.572626
ENSMUSG00000000263   8.914531
ENSMUSG00000000275  16.467614
ENSMUSG00000000276  11.135824
ENSMUSG00000000290  12.362938
ENSMUSG00000000296  12.052529
ENSMUSG00000000301  17.342377
ENSMUSG00000000303  13.877282
ENSMUSG00000000305  10.082684
ENSMUSG00000000308   8.914531
ENSMUSG00000000320   9.837990
ENSMUSG00000000326  17.896285
ENSMUSG00000000340  15.355382
ENSMUSG00000000374  14.104101
ENSMUSG00000000394   8.914531
ENSMUSG00000000399  16.059257
ENSMUSG00000000409  10.228724
ENSMUSG00000000420  14.473496
ENSMUSG00000000435   8.914531
ENSMUSG00000000440  11.681228
ENSMUSG000

ENSMUSG00000002963  13.846266
ENSMUSG00000002968  13.896760
ENSMUSG00000002983  10.271482
ENSMUSG00000002984  13.131079
ENSMUSG00000002985  23.009049
ENSMUSG00000002992  16.924248
ENSMUSG00000003031  14.296182
ENSMUSG00000003032  10.584320
ENSMUSG00000003033  13.598654
ENSMUSG00000003037  14.929383
ENSMUSG00000003039  14.162793
ENSMUSG00000003051   9.476908
ENSMUSG00000003053  20.002570
ENSMUSG00000003062  11.792565
ENSMUSG00000003068  15.157343
ENSMUSG00000003070   8.914531
ENSMUSG00000003072  15.671974
ENSMUSG00000003099  13.968725
ENSMUSG00000003119  13.243440
ENSMUSG00000003131  14.172841
ENSMUSG00000003135  12.979739
ENSMUSG00000003153  10.182178
ENSMUSG00000003161  13.459285
ENSMUSG00000003184  14.775617
ENSMUSG00000003200  12.693572
ENSMUSG00000003206  10.311702
ENSMUSG00000003208  10.656534
ENSMUSG00000003226  15.309850
ENSMUSG00000003227   8.914531
ENSMUSG00000003228  12.269676
ENSMUSG00000003233  13.124291
ENSMUSG00000003235  14.053697
ENSMUSG00000003269  12.636400
ENSMUSG000

ENSMUSG00000005804  13.014720
ENSMUSG00000005813  14.116672
ENSMUSG00000005824   9.912949
ENSMUSG00000005836  11.641847
ENSMUSG00000005864   8.914531
ENSMUSG00000005871  13.951845
ENSMUSG00000005883   9.310575
ENSMUSG00000005886  14.526830
ENSMUSG00000005892   8.914531
ENSMUSG00000005893  14.599469
ENSMUSG00000005897  12.915982
ENSMUSG00000005899  13.117213
ENSMUSG00000005907  14.353893
ENSMUSG00000005947   9.944186
ENSMUSG00000005949  12.885666
ENSMUSG00000005950   8.914531
ENSMUSG00000005951  15.004698
ENSMUSG00000005952   9.594775
ENSMUSG00000005958   9.974248
ENSMUSG00000005973  11.517318
ENSMUSG00000005994   8.914531
ENSMUSG00000006005  14.666127
ENSMUSG00000006021  12.499331
ENSMUSG00000006024  14.946410
ENSMUSG00000006057  14.221475
ENSMUSG00000006058  13.525092
ENSMUSG00000006127  13.250856
ENSMUSG00000006134  14.352414
ENSMUSG00000006169  14.787577
ENSMUSG00000006205  10.348853
ENSMUSG00000006216   8.914531
ENSMUSG00000006219  10.451810
ENSMUSG00000006235  10.269771
ENSMUSG000

ENSMUSG00000013160  14.604616
ENSMUSG00000013236  11.446110
ENSMUSG00000013275  11.210006
ENSMUSG00000013418   8.914531
ENSMUSG00000013465  13.307974
ENSMUSG00000013584   9.285081
ENSMUSG00000013593  16.477358
ENSMUSG00000013629  12.049564
ENSMUSG00000013643   8.914531
ENSMUSG00000013662  15.080531
ENSMUSG00000013663  15.993688
ENSMUSG00000013698  13.048716
ENSMUSG00000013707  10.951391
ENSMUSG00000013787  14.662041
ENSMUSG00000013833  12.674216
ENSMUSG00000013846  16.526445
ENSMUSG00000013921   9.594775
ENSMUSG00000013936   8.914531
ENSMUSG00000013974   9.646687
ENSMUSG00000014030  10.084763
ENSMUSG00000014074  12.627295
ENSMUSG00000014075  10.550889
ENSMUSG00000014077  17.246367
ENSMUSG00000014158   9.843602
ENSMUSG00000014164  12.648926
ENSMUSG00000014232  12.037152
ENSMUSG00000014245  11.592389
ENSMUSG00000014294  14.790413
ENSMUSG00000014313  16.515914
ENSMUSG00000014349  14.483052
ENSMUSG00000014351   8.914531
ENSMUSG00000014355  14.570907
ENSMUSG00000014361  13.668797
ENSMUSG000

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [16]:
%%R
tcdd_dose_detail.vec.train <-
   tcdd_dose_detail_vec_tis_of_interest[training_indices]
tcdd_dose_detail.vec.test <-
   tcdd_dose_detail_vec_tis_of_interest[-training_indices]

# print(gtex_tissue_detail.vec.train)
print(length(unique(tcdd_dose_detail.vec.train)))

[1] 2


In [17]:
%%R
saveRDS(tcdd_dose_detail.vec.train,file=paste(OUT_DIR,"tcdd_dose_detail_vec_train0.3vs0_time_course.Rds",sep=""))

In [18]:
%%R
cv_fold_indices <- caret::createFolds(tcdd_dose_detail.vec.train,
                                      k = N_FOLDS)
print(cv_fold_indices)

$Fold01
[1]  4 11 17 32 47 50 65 76

$Fold02
 [1] 34 37 42 51 57 64 69 72 89 90

$Fold03
 [1]  3  9 13 14 33 46 59 73 85 91

$Fold04
[1] 16 18 30 35 58 63 71 88

$Fold05
[1]  6  8 19 23 31 40 60 78 79

$Fold06
 [1]  7 15 20 27 36 44 54 67 81 83

$Fold07
[1] 24 26 38 43 45 55 61 75 87

$Fold08
[1]  5 10 21 22 41 48 74 84 86

$Fold09
[1]  2 25 29 39 53 62 70 77 82

$Fold10
[1]  1 12 28 49 52 56 66 68 80



In [19]:
%%R
binary_tcdd_dose_annotations <- unique(tcdd_dose_detail.vec)
print(binary_tcdd_dose_annotations)

[1] 0.0 0.3


In [20]:
%%R
full_rxn_pca_results.nls <- list()
rxn_id_2_result_file_idx.nls <- list()

In [21]:
%%R
n_rxns <- length(rxns)
print(n_rxns)
result_idx <- 1
for(rxn_id_idx in seq(1:n_rxns)){
   rxn_id <- rxns[rxn_id_idx]
   rxn_pca <-
      prcomp(t(vst.count.mtx.train[rxn2ensembls.nls[[rxn_id]], ]), scale. = T)
   full_rxn_pca_results.nls[[rxn_id]] <- rxn_pca
   rxn_id_2_result_file_idx.nls[[rxn_id]] <- result_idx
   rxn_pca.nls[[rxn_id]] <-
      rxn_pca$x[, 1] # 1st principal component coordinate within this reaction-space for each sample
   if(mod(rxn_id_idx,100) == 0){
      print(paste("Processed ",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      flush.console()
   }
   if(mod(rxn_id_idx,1000) == 0){
      print(paste("Storing PCA objects containing reactions ",rxn_id_idx-1000,
                  "-",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      saveRDS(full_rxn_pca_results.nls,
              paste(OUT_DIR, "full_rxn_pca_results_nls",rxn_id_idx-1000,
                    "-",rxn_id_idx,"0.3vs0_time_course.Rds", sep=""))
      full_rxn_pca_results.nls <- list()
      gc()
      result_idx <- result_idx + 1
   }
}

[1] 9825
[1] "Processed 100 of 9825 reactions (1%)..."
[1] "Processed 200 of 9825 reactions (2%)..."
[1] "Processed 300 of 9825 reactions (3.1%)..."
[1] "Processed 400 of 9825 reactions (4.1%)..."
[1] "Processed 500 of 9825 reactions (5.1%)..."
[1] "Processed 600 of 9825 reactions (6.1%)..."
[1] "Processed 700 of 9825 reactions (7.1%)..."
[1] "Processed 800 of 9825 reactions (8.2%)..."
[1] "Processed 900 of 9825 reactions (9.2%)..."
[1] "Processed 1000 of 9825 reactions (10.2%)..."
[1] "Storing PCA objects containing reactions 0-1000 of 9825 reactions (10.2%)..."
[1] "Processed 1100 of 9825 reactions (11.2%)..."
[1] "Processed 1200 of 9825 reactions (12.2%)..."
[1] "Processed 1300 of 9825 reactions (13.2%)..."
[1] "Processed 1400 of 9825 reactions (14.3%)..."
[1] "Processed 1500 of 9825 reactions (15.3%)..."
[1] "Processed 1600 of 9825 reactions (16.3%)..."
[1] "Processed 1700 of 9825 reactions (17.3%)..."
[1] "Processed 1800 of 9825 reactions (18.3%)..."
[1] "Processed 1900 of 9825 re

In [22]:
%%R
# store remaining PCA objects and removing from RAM
saveRDS(rxn_id_2_result_file_idx.nls,
        paste(OUT_DIR,"rxn_id_2_result_file_idx_nls0.3vs0_time_course.Rds",sep=""))
saveRDS(full_rxn_pca_results.nls,
        paste(OUT_DIR, "full_rxn_pca_results_nls0.3vs0_time_course.Rds", sep=""))
rm(full_rxn_pca_results.nls)
gc()

           used  (Mb) gc trigger  (Mb) max used  (Mb)
Ncells  6950689 371.3   13075665 698.4 11898582 635.5
Vcells 15945280 121.7   25842636 197.2 25842636 197.2


In [23]:
%%R
# compare informaction content of below files with pca plots or similar
saveRDS(rxn_pca.nls, paste(OUT_DIR, "rxn_pca_nls0.3vs0_time_course.Rds", sep = ""))
saveRDS(vst.count.mtx.train,
        paste(OUT_DIR, "vst_count_mtx_train0.3vs0_time_course.Rds", sep = ""))

In [24]:
%%R
for (cv_fold in names(cv_fold_indices)) {
  cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
}

In [25]:
%%R
# print(tissue_annotation)
# print(binary_tcdd_dose_annotations)
# print(paste("Processing tissue annotation:", tissue_annotation))
# print(length(binary_tcdd_dose_detail_vec.test.cv_test_list))
# print(sum(tcdd_dose_detail.vec.train.cv_test == tissue_annotation))
# print(length(rxns))

# binary_tcdd_dose_annotations <- c(0.00, 30.00, 0.01, 0.03, 0.10, 0.30, 1.00, 3.00, 10.00)

formatted_annotations <- format(binary_tcdd_dose_annotations, nsmall = 2)

formatted_annotations <- trimws(formatted_annotations)

binary_tcdd_dose_annotations <- formatted_annotations

print(binary_tcdd_dose_annotations)
for (annotation in binary_tcdd_dose_annotations) {
    print(annotation)
}

[1] "0.00" "0.30"
[1] "0.00"
[1] "0.30"


In [26]:
%%R
# main loop
for (rxn_id_idx in seq(1:length(rxns))) {
   rxn_id <- rxns[rxn_id_idx]
   ensembl_ids <- rxn2ensembls.nls[[rxn_id]]
   
   mean_misclass_rate <- list()
   sum_ari <- 0

   for (cv_fold in names(cv_fold_indices)) {
      cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
      
      vst.count.mtx.train.cv_train <-
         vst.count.mtx.train[, -cur_cv_fold_indices] # 4/5ths of training features
      vst.count.mtx.train.cv_test <-
         vst.count.mtx.train[, cur_cv_fold_indices] # 1/5th of training features
      
      tcdd_dose_detail.vec.train.cv_train <-
         tcdd_dose_detail.vec.train[-cur_cv_fold_indices] # 4/5ths of training labels
      tcdd_dose_detail.vec.train.cv_test <-
         tcdd_dose_detail.vec.train[cur_cv_fold_indices] # 1/5th of training labels
      
#        print(length(vst.count.mtx.train.cv_train))
#        print(length(gtex_tissue_detail.vec.train.cv_train))
       
      binary_tcdd_dose_detail_vec.test.cv_test_list <- list()
      for (tissue_annotation in binary_tcdd_dose_annotations) {
#          print(tcdd_dose_detail.vec.train.cv_test)
#          print("-------------")
#          print(tissue_annotation)
#          print(binary_tcdd_dose_detail_vec.test.cv_test_list)
         binary_tcdd_dose_detail_vec.test.cv_test_list[[as.character(tissue_annotation)]] <-
            (as.character(tcdd_dose_detail.vec.train.cv_test) == as.character(tissue_annotation))
      }
      
      cv_train.expr_mat <-
         t(vst.count.mtx.train.cv_train[ensembl_ids, ])
      cv_test.expr_mat <-
         t(vst.count.mtx.train.cv_test[ensembl_ids, ])
#        print(dim(cv_train.expr_mat))
#        print(length(gtex_tissue_detail.vec.train.cv_train))
      
      rxn_knn_calls <- class::knn(train = cv_train.expr_mat,
                                  test = cv_test.expr_mat,
                                  cl = tcdd_dose_detail.vec.train.cv_train)
      
      # calculate & store adjusted rand index
      cur_ari <- pdfCluster::adj.rand.index(rxn_knn_calls,
                                            tcdd_dose_detail.vec.train.cv_test)
      sum_ari <- cur_ari + sum_ari
      
      # for each tissue, calculate misclassification rate
      for (tissue_annotation in binary_tcdd_dose_annotations) {
         cur_rxn_knn_calls <- (rxn_knn_calls == tissue_annotation)
            
         # calculate misclassification rate (https://stat.ethz.ch/pipermail/r-help/2011-September/288885.html)
         tab <- table(cur_rxn_knn_calls,
                      binary_tcdd_dose_detail_vec.test.cv_test_list[[tissue_annotation]])
        # print(tab)
         cur_misclass_rate <- 1 - sum(diag(tab)) / sum(tab)
        # print(paste("Misclass rate = 1 - ",sum(diag(tab))," / ",sum(tab)," = ", cur_misclass_rate,"...",sep=""))
         sum_misclass_rate <- cur_misclass_rate
         if (!is.null(mean_misclass_rate[[tissue_annotation]])) {
           sum_misclass_rate <- sum_misclass_rate + mean_misclass_rate[[tissue_annotation]]
         }
         mean_misclass_rate[[tissue_annotation]] <- sum_misclass_rate
      }
   }
   for(tissue_annotation in binary_tcdd_dose_annotations){
      mean_misclass_rate[[tissue_annotation]] <- (mean_misclass_rate[[tissue_annotation]] / N_FOLDS)
   }
   mean_ari <- sum_ari / N_FOLDS
   ecount <- length(ensembl_ids)
   
   rxn_knn_misclass_rate.nls[[rxn_id]] <- mean_misclass_rate
   assign("mean_misclass_rate",NULL,envir = .GlobalEnv)
   
   rxn_knn_ari.nls[[rxn_id]] <- mean_ari
   rxn_knn_ecount.nls[[rxn_id]] <- ecount
   
   count <- count + 1
   if (mod(count, 10) == 0) {
      print(
         paste(
            "Last RXN_ID = ",
            rxn_id,
            ": Last ARI = ",
            mean_ari,
            ": Last ECOUNT = ",
            ecount,
            ": Last Lung MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Lung"]],
            ": Last Uterus MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Uterus"]],
            ". Now ",
            round(1.0 - count / length(rxns),3) * 100,
            "% remaining..."
         )
      )
      flush.console()
   }
}

[1] "Last RXN_ID =  R-MMU-749456 : Last ARI =  0.959214501510574 : Last ECOUNT =  178 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-9021601 : Last ARI =  0.819192317813954 : Last ECOUNT =  24 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-3108203 : Last ARI =  1 : Last ECOUNT =  15 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9838627 : Last ARI =  0.448225143385567 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-193679 : Last ARI =  0.202140563586347 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-194544 : Last ARI =  0.281600149248334 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.4 % remaining..."
[1] "Last RXN_ID =  R-MMU

[1] "Last RXN_ID =  R-MMU-8949580 : Last ARI =  0.901709401709402 : Last ECOUNT =  18 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-9692137 : Last ARI =  0.181267739729962 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-450580 : Last ARI =  0.960176991150443 : Last ECOUNT =  12 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-6791222 : Last ARI =  0.914770057066129 : Last ECOUNT =  61 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9696268 : Last ARI =  0.960176991150443 : Last ECOUNT =  41 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-1912394 : Last ARI =  0.746554071906185 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.4 % remaining..."
[1] "La

[1] "Last RXN_ID =  R-MMU-3928599 : Last ARI =  -0.0324256588085693 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-3928625 : Last ARI =  0.596554252552171 : Last ECOUNT =  17 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-3928657 : Last ARI =  0.400346983075378 : Last ECOUNT =  10 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9034539 : Last ARI =  0.107480774602793 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-983156 : Last ARI =  1 : Last ECOUNT =  242 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-174119 : Last ARI =  0.782026694234271 : Last ECOUNT =  18 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.4 % remaining..."
[1] "Last RXN_ID =  R

[1] "Last RXN_ID =  R-MMU-5228523 : Last ARI =  0.918181818181818 : Last ECOUNT =  33 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-2395328 : Last ARI =  0.146103678127847 : Last ECOUNT =  5 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-8852134 : Last ARI =  0.830502603772128 : Last ECOUNT =  6 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-354124 : Last ARI =  0.765775233423419 : Last ECOUNT =  13 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-429415 : Last ARI =  0.781481481481481 : Last ECOUNT =  13 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-9714691 : Last ARI =  0.653830996127069 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84.3 % remaining..."
[1] "Last

[1] "Last RXN_ID =  R-MMU-2426496 : Last ARI =  0.656026837704514 : Last ECOUNT =  10 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.8 % remaining..."
[1] "Last RXN_ID =  R-NUL-2467092 : Last ARI =  0.71819544321991 : Last ECOUNT =  7 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-168162 : Last ARI =  0.596030331324449 : Last ECOUNT =  6 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-445079 : Last ARI =  0.718188860484933 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-8856808 : Last ARI =  0.857264957264957 : Last ECOUNT =  19 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-5607725 : Last ARI =  0.665269583743035 : Last ECOUNT =  14 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  79.3 % remaining..."
[1] "Last 

...

[1] "Last RXN_ID =  R-MMU-8940998 : Last ARI =  0.0164556599256122 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  25 % remaining..."
[1] "Last RXN_ID =  R-MMU-166869 : Last ARI =  0.236751627845596 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-76031 : Last ARI =  0.190150258638295 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-201521 : Last ARI =  0.193858874879735 : Last ECOUNT =  5 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9701485 : Last ARI =  0.193858874879735 : Last ECOUNT =  5 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-2161187 : Last ARI =  0.0231557926799618 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  24.5 % remaining..."
[1] "Last RXN_

[1] "Last RXN_ID =  R-MMU-437092 : Last ARI =  0.308059516519964 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  20 % remaining..."
[1] "Last RXN_ID =  R-MMU-173597 : Last ARI =  0.144966671916931 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-5663185 : Last ARI =  0.637211068184519 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-111285 : Last ARI =  0.00862056566281918 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9758661 : Last ARI =  1 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-433089 : Last ARI =  0.1589495586286 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  19.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-264679

[1] "Last RXN_ID =  R-MMU-9724745 : Last ARI =  0.0950359120413437 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  15 % remaining..."
[1] "Last RXN_ID =  R-MMU-9010872 : Last ARI =  0.000876321505981831 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-194641 : Last ARI =  0.137212273069504 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-202939 : Last ARI =  -0.0121248494051685 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9831009 : Last ARI =  0.288435243401887 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9833697 : Last ARI =  0.239940982620891 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  14.5 % remaining..."
[1] "Las

[1] "Last RXN_ID =  R-MMU-110352 : Last ARI =  -0.00163402659171232 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  10 % remaining..."
[1] "Last RXN_ID =  R-MMU-975916 : Last ARI =  0.20358610617405 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-417858 : Last ARI =  -0.0880551989887763 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-446214 : Last ARI =  -0.0527976063761198 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-5578712 : Last ARI =  0.248672497023061 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-352052 : Last ARI =  0.381909646297732 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  9.5 % remaining..."
[1] "Last RXN_ID

[1] "Last RXN_ID =  R-MMU-451056 : Last ARI =  0.0430330263186738 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-1640164 : Last ARI =  0.472238104274375 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-1482897 : Last ARI =  0.146913955825163 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-5340195 : Last ARI =  0.206725794575528 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9708866 : Last ARI =  0.157649209147661 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-8959510 : Last ARI =  0.230705576685883 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  4.4 % remaining..."
[1] "Last RXN_ID

In [27]:
%%R
saveRDS(
   rxn_knn_misclass_rate.nls,
   paste(OUT_DIR, "toi_rxn_knn_misclass_rate_nls0.3vs0_time_course.Rds", sep = "")
)
saveRDS(rxn_knn_ari.nls,
        paste(OUT_DIR, "toi_rxn_knn_ari_nls0.3vs0_time_course.Rds", sep = ""))
saveRDS(rxn_knn_ecount.nls,
        paste(OUT_DIR, "toi_rxn_knn_ecount_nls0.3vs0_time_course.Rds", sep = ""))

In [28]:
%%R
d <- data.frame(
   RXN_ID = names(rxn2ensembls.nls),
   MISCLASS = unlist(rxn_knn_misclass_rate.nls),
   ARI = unlist(rxn_knn_ari.nls),
   ECOUNT = unlist(rxn_knn_ecount.nls)
)
print(d)
saveRDS(d, paste(OUT_DIR, "toi_summary_df0.3vs0_time_course.Rds", sep = ""))

                          RXN_ID MISCLASS           ARI ECOUNT
R-MMU-170666.0.00   R-MMU-170666        0  0.6724799978     14
R-MMU-170666.0.30   R-MMU-170671        0  0.6724799978     14
R-MMU-170671.0.00   R-MMU-170674        0  0.6724799978     14
R-MMU-170671.0.30   R-MMU-170686        0  0.6724799978     14
R-MMU-170674.0.00   R-MMU-380073        0  0.9147700571    182
R-MMU-170674.0.30   R-MMU-392187        0  0.8795684838     22
R-MMU-170686.0.00   R-MMU-392195        0  0.8795684838     22
R-MMU-170686.0.30   R-MMU-392202        0  0.8795684838     22
R-MMU-380073.0.00   R-MMU-749454        0  0.9592145015    178
R-MMU-380073.0.30   R-MMU-749456        0  0.9592145015    178
R-MMU-392187.0.00   R-MMU-751001        0  0.8300735343     21
R-MMU-392187.0.30  R-MMU-8964229        0  0.4500074449      5
R-MMU-392195.0.00  R-MMU-8964242        0  0.4500074449      5
R-MMU-392195.0.30  R-MMU-8964329        0  0.4500074449      5
R-MMU-392202.0.00  R-MMU-8982012        0  0.8662375972

R-MMU-205112.0.30  R-MMU-5654397        0  0.2047301795     16
R-MMU-205117.0.00  R-MMU-5654399        0  0.2047301795     16
R-MMU-205117.0.30  R-MMU-5654402        0  0.7698796516     20
R-MMU-209532.0.00  R-MMU-5654404        0  0.2253113676     16
R-MMU-209532.0.30  R-MMU-5654406        0  0.5116979922     18
R-MMU-209566.0.00  R-MMU-5654407        0  0.2253113676     16
R-MMU-209566.0.30  R-MMU-5654408        0  0.5265152759     12
R-MMU-9012761.0.00 R-MMU-5654409        0  0.5265152759     12
R-MMU-9012761.0.30 R-MMU-5654413        0  0.7449308196     17
R-MMU-3247837.0.00 R-MMU-5654416        0  0.4426502832     15
R-MMU-3247837.0.30 R-MMU-5654418        0  0.2666719966     14
R-MMU-3247840.0.00 R-MMU-5654422        0  0.2666719966     14
R-MMU-3247840.0.30 R-MMU-5654423        0  0.7414621514     16
R-MMU-3247843.0.00 R-MMU-5654425        0  0.4765014376     14
R-MMU-3247843.0.30 R-MMU-5654426        0  0.9555555556     18
R-MMU-3247844.0.00 R-MMU-5654428        0  0.4765014376

R-MMU-5654397.0.30 R-MMU-9753126        0  0.0988909475      5
R-MMU-5654399.0.00  R-MMU-514604        0 -0.0872484306      2
R-MMU-5654399.0.30  R-MMU-975389        0  0.4443771812      4
R-MMU-5654402.0.00 R-MMU-1169394        0  0.8698965432      5
R-MMU-5654402.0.30 R-MMU-1169398        0  0.7926372603      5
R-MMU-5654404.0.00 R-MMU-1169402        0  0.5878720146      6
R-MMU-5654404.0.30 R-MMU-1169403        0  0.5530070909      4
R-MMU-5654406.0.00 R-MMU-1169405        0  0.7468012567      5
R-MMU-5654406.0.30 R-MMU-1169406        0  0.9461538462     12
R-MMU-5654407.0.00 R-MMU-1678842        0  0.9601769912     13
R-MMU-5654407.0.30 R-MMU-1678843        0  0.6222187899      5
R-MMU-5654408.0.00 R-MMU-5653754        0  0.7839278093     21
R-MMU-5654408.0.30 R-MMU-5653756        0  0.8346320346     19
R-MMU-5654409.0.00 R-MMU-9833973        0  0.8291110447      5
R-MMU-5654409.0.30  R-MMU-426240        0  0.4071331808     10
R-MMU-5654413.0.00  R-MMU-199050        0  0.2856764960

R-MMU-5654664.0.30  R-MMU-389158        0  0.6874225151      9
R-MMU-5654667.0.00  R-MMU-389348        0  0.3375869523      8
R-MMU-5654667.0.30  R-MMU-389350        0  0.3517398326      8
R-MMU-5654669.0.00  R-MMU-389352        0  0.3827386809      7
R-MMU-5654669.0.30  R-MMU-389354        0  0.3827386809      7
R-MMU-5654672.0.00  R-MMU-389381        0  0.1449377171      6
R-MMU-5654672.0.30  R-MMU-389758        0  0.5976909797     22
R-MMU-5654673.0.00  R-MMU-389759        0  0.3210288713      7
R-MMU-5654673.0.30  R-MMU-389762        0  0.1754011376      5
R-MMU-5654677.0.00  R-MMU-434836        0  0.0057533289      3
R-MMU-5654677.0.30  R-MMU-452100        0  0.1846819847      6
R-MMU-5654679.0.00 R-MMU-8852200        0  0.4270997667     17
R-MMU-5654679.0.30 R-MMU-8855381        0  0.5216892735     18
R-MMU-5654684.0.00 R-MMU-8857925        0  0.8276353276     15
R-MMU-5654684.0.30 R-MMU-9706312        0  0.2324680943      2
R-MMU-5654690.0.00 R-MMU-8849348        0  0.2631212269

R-MMU-9753126.0.30  R-MMU-450580        0  0.9601769912     12
R-MMU-514604.0.00    R-MMU-72103        0  0.9555555556     43
R-MMU-514604.0.30  R-MMU-9770119        0  1.0000000000     69
R-MMU-975389.0.00  R-MMU-9770141        0  1.0000000000    123
R-MMU-975389.0.30  R-MMU-9770142        0  1.0000000000    132
R-MMU-1169394.0.00 R-MMU-9770145        0  1.0000000000    145
R-MMU-1169394.0.30 R-MMU-9770236        0  1.0000000000    119
R-MMU-1169398.0.00 R-MMU-6798748        0  0.9555555556    106
R-MMU-1169398.0.30 R-MMU-6800434        0  0.9555555556    134
R-MMU-1169402.0.00 R-MMU-6791218        0  0.8703256126     68
R-MMU-1169402.0.30 R-MMU-6791222        0  0.9147700571     61
R-MMU-1169403.0.00 R-MMU-1605595        0  0.8643356643      3
R-MMU-1169403.0.30 R-MMU-1605624        0  0.6285063208      6
R-MMU-1169405.0.00 R-MMU-1605717        0  0.0124331515      1
R-MMU-1169405.0.30 R-MMU-6798751        0  0.9193914927    105
R-MMU-1169406.0.00 R-MMU-9840795        0  0.4744775356

...

R-MMU-417908.0.30   R-MMU-193073        0  0.5110578684      9
R-MMU-3134953.0.00  R-MMU-193997        0  0.2291942248      3
R-MMU-3134953.0.30  R-MMU-265301        0  0.2373630080      2
R-MMU-3134962.0.00  R-MMU-388605        0  0.2314607253      1
R-MMU-3134962.0.30  R-MMU-469659        0  0.4550732434      2
R-MMU-189053.0.00  R-MMU-9623061        0  0.2333621242      2
R-MMU-189053.0.30  R-MMU-9623076        0  0.2333621242      2
R-MMU-189069.0.00  R-MMU-9705713        0  0.0427475602      2
R-MMU-189069.0.30  R-MMU-9705714        0  0.0657920168      2
R-MMU-191101.0.00  R-MMU-5212679        0 -0.0020421268     14
R-MMU-191101.0.30  R-MMU-5694018        0  0.5798459898      2
R-MMU-191108.0.00   R-MMU-209815        0  0.4148577793      1
R-MMU-191108.0.30   R-MMU-209840        0  0.2245243613      3
R-MMU-5659861.0.00  R-MMU-209925        0  0.2245243613      3
R-MMU-5659861.0.30  R-MMU-209973        0  0.4148577793      1
R-MMU-9023617.0.00  R-MMU-350901        0  0.4148577793

R-MMU-140851.0.30  R-MMU-5138441        0  0.3288411711      3
R-MMU-2404137.0.00  R-MMU-508681        0  0.9147700571      6
R-MMU-2404137.0.30  R-MMU-549505        0  0.8609239032      7
R-MMU-2453855.0.00 R-MMU-5663147        0  0.8749470482      3
R-MMU-2453855.0.30 R-MMU-5663263        0  0.8652751076      5
R-MMU-975608.0.00  R-MMU-5663294        0  0.9555555556      4
R-MMU-975608.0.30  R-MMU-5667072        0  0.7483392084      3
R-MMU-71188.0.00   R-MMU-5667077        0  1.0000000000      3
R-MMU-71188.0.30     R-MMU-74885        0  0.0497271206      4
R-MMU-449937.0.00  R-MMU-8942208        0  0.2644657686      1
R-MMU-449937.0.30   R-MMU-508749        0  0.0863832693      2
R-MMU-179883.0.00   R-MMU-549491        0  0.7788358888      3
R-MMU-179883.0.30  R-MMU-5663158        0  0.7788358888      3
R-MMU-382057.0.00   R-MMU-210444        0  0.4184293607      4
R-MMU-382057.0.30   R-MMU-264615        0  0.3599044474      4
R-MMU-382061.0.00   R-MMU-376369        0  0.3454644014

R-MMU-9659568.0.30 R-MMU-6808566        0  0.4074903587      1
R-MMU-5653957.0.00  R-MMU-192036        0  0.3007059089      3
R-MMU-5653957.0.30  R-MMU-192160        0  0.3007059089      3
R-MMU-727807.0.00   R-MMU-193758        0  0.3007059089      3
R-MMU-727807.0.30   R-MMU-193781        0  0.3007059089      3
R-MMU-378956.0.00   R-MMU-193800        0  0.3007059089      3
R-MMU-378956.0.30   R-MMU-193841        0  0.3007059089      3
R-MMU-378978.0.00  R-MMU-2161549        0  0.3007059089      3
R-MMU-378978.0.30  R-MMU-2161614        0  0.3007059089      3
R-MMU-391378.0.00  R-MMU-2855252        0  0.3366389436      5
R-MMU-391378.0.30  R-MMU-5615668        0  0.3007059089      3
R-MMU-6786034.0.00 R-MMU-9758682        0  0.3007059089      3
R-MMU-6786034.0.30 R-MMU-2077477        0  0.7016387439      3
R-MMU-70342.0.00   R-MMU-5610735        0  0.0212275502      2
R-MMU-70342.0.30   R-MMU-5610737        0  0.0138981458      4
R-MMU-4084976.0.00 R-MMU-5635861        0  0.2395947888

R-MMU-193533.0.30  R-MMU-2562564        0  0.5431423108      8
R-MMU-2066781.0.00 R-MMU-2569057        0  0.4710436810      7
R-MMU-2066781.0.30 R-MMU-3371360        0  0.5204625043      6
R-MMU-390224.0.00  R-MMU-5213464        0  0.2293994910      2
R-MMU-390224.0.30  R-MMU-5213466        0  0.2293994910      2
R-MMU-200410.0.00  R-MMU-5218905        0  0.2293994910      2
R-MMU-200410.0.30  R-MMU-5357780        0  0.2677327023      9
R-MMU-6798372.0.00 R-MMU-5357828        0  0.6048205758      5
R-MMU-6798372.0.30 R-MMU-5634221        0  0.3347036069      6
R-MMU-6798374.0.00   R-MMU-83656        0  0.3846306947      5
R-MMU-6798374.0.30 R-MMU-9693978        0  0.2293994910      2
R-MMU-9659557.0.00 R-MMU-9697747        0  0.5204625043      6
R-MMU-9659557.0.30 R-MMU-9697750        0  0.5204625043      6
R-MMU-73647.0.00   R-MMU-9793680        0  0.4582809663     13
R-MMU-73647.0.30   R-MMU-9796379        0  0.4277991210     12
R-MMU-9008063.0.00 R-MMU-9819106        0  0.4244246174

R-MMU-9006133.0.30  R-MMU-190093        0  0.4722381043      1
R-MMU-9625102.0.00  R-MMU-425483        0  0.0776206976      3
R-MMU-9625102.0.30  R-MMU-192335        0  0.0385440599      1
R-MMU-9625109.0.00  R-MMU-193369        0  0.0385440599      1
R-MMU-9625109.0.30  R-MMU-389889        0  0.0609873515      2
R-MMU-8849463.0.00 R-MMU-1067651        0  0.5236212222      5
R-MMU-8849463.0.30 R-MMU-1067659        0  0.5236212222      5
R-NUL-9625758.0.00 R-MMU-1067676        0  0.3620724743      3
R-NUL-9625758.0.30 R-MMU-1067688        0  0.5236212222      5
R-NUL-9625772.0.00  R-MMU-109858        0  0.5622866186      8
R-NUL-9625772.0.30 R-MMU-1112510        0  0.5236212222      5
R-MMU-426489.0.00  R-MMU-1112514        0  0.5236212222      5
R-MMU-426489.0.30  R-MMU-1112690        0  0.5148798587      7
R-MMU-426522.0.00  R-MMU-1112703        0  0.5579354143      6
R-MMU-426522.0.30  R-MMU-1112708        0  0.5579354143      6
R-MMU-156682.0.00  R-MMU-1112755        0  0.5788108351

In [29]:
%%R
pid <- read.table(paste(OUT_DIR,"tcdd_project_id0.3vs0_time_course.txt",sep=""),header=FALSE)
sid <- read.table(paste(OUT_DIR,"tcdd_sample_id0.3vs0_time_course.txt",sep=""), header=FALSE)
sex <- read.table(paste(OUT_DIR, "tcdd_gender0.3vs0_time_course.txt", sep=""), header=FALSE)
print(sex)

In [30]:
%%R
library(htmlwidgets)
min_misclass_pca <-
   prcomp(t(vst.count.mtx.train), scale. = T)
pca.d <- data.frame(
   PC1 = min_misclass_pca$x[, 1],
   PC2 = min_misclass_pca$x[, 2],
   PC3 = min_misclass_pca$x[, 3],
   Section = tcdd_dose_detail.vec.train,
   Project_id = pid$V1,
   Sample_id = sid$V1
)

ggplot(pca.d, aes(x = PC1, y = PC2, colour = Section)) +
   geom_point(size = 3) +  # 绘制点，指定点的大小
   geom_text(aes(label = paste(Project_id, Sample_id)), vjust = -1, hjust = 1, size = 2) +  # 添加标签
   scale_colour_manual(values = c("0" = "red", "0.3" = "green")) +  # 手动指定颜色
   theme_bw()

p <- plot_ly(
   data = pca.d,
   x = ~PC1,
   y = ~PC2,
   z = ~PC3,
   type = "scatter3d",
   mode = "markers",
   marker = list(
     color = as.factor(pca.d$Section),  # 将 Section 转换为因子
     colors = c("red", "green"),  # 定义颜色
     size = 5
   ),
   text = ~paste("Project ID:", Project_id, "Sample ID:", Sample_id)  # 在悬停文本中显示 Project ID
)
saveWidget(p, "plotly_chart0.3vs0_time_course.html", selfcontained = TRUE)